In [13]:
%matplotlib widget
import matplotlib.pyplot as plt
import matplotlib.cm
import matplotlib.colors
plt.rcParams['figure.figsize'] = (9, 7)

import numpy as np

from lsst.daf.persistence import Butler
import lsst.display.matplotlib
from lsst.afw.display import Display, GREEN
Display.setDefaultBackend("matplotlib")

from pfs.datamodel import PfsDesign, TargetType, FiberStatus

In [44]:
import astropy.io.fits
with astropy.io.fits.open("/home/pfs/pfs/sim2d-151/catalog_9.fits") as fits:
    catalog = fits[1].data
print(catalog.dtype.names)
print(catalog.objId)

('catId', 'objId', 'tract', 'patch', 'type', 'redshift', 'm_g', 'm_r', 'm_i', 'm_z', 'm_y', 'em_g', 'em_r', 'em_i', 'em_z', 'em_y', 'flux_g', 'flux_r', 'flux_i', 'flux_z', 'flux_y', 'e_flux_g', 'e_flux_r', 'e_flux_i', 'e_flux_z', 'e_flux_y', 'T_eff', 'log_g', 'Fe_H', 'alpha_Fe', 'rv')
[  0   1   2   3   4   5   6   7   8   9  10  11  12  13  14  15  16  17
  18  19  20  21  22  23  24  25  26  27  28  29  30  31  32  33  34  35
  36  37  38  39  40  41  42  43  44  45  46  47  48  49  50  51  52  53
  54  55  56  57  58  59  60  61  62  63  64  65  66  67  68  69  70  71
  72  73  74  75  76  77  78  79  80  81  82  83  84  85  86  87  88  89
  90  91  92  93  94  95  96  97  98  99 100 101 102 103 104 105 106 107
 108 109 110 111 112 113 114 115 116 117 118 119 120 121 122 123 124 125
 126 127 128 129 130 131 132 133 134 135 136 137 138 139 140 141 142 143
 144 145 146 147 148 149 150 151 152 153 154 155 156 157 158 159 160 161
 162 163 164 165 166 167 168 169 170 171 172 173 174 175 

-----

In [56]:
def updatePfsDesign(design: PfsDesign, objId: np.ndarray):
    """Update PfsDesign to include realistic flux standards

    Parameters
    ----------
    design : `pfs.datamodel.PfsDesign`
        PfsDesign to update (in-place).
    objId : `numpy.ndarray` of `int`
        Object IDs to use for flux standards.
    """
    select = (design.targetType == TargetType.FLUXSTD) & (design.spectrograph == 1)
    design.catId[select] = 9
    design.objId[select] = objId[:select.sum()]

    for index in np.argwhere(select):
        dd = index.item()
        cc = np.argwhere(catalog.objId == design.objId[index]).item()
        design.filterNames[dd] = ["g_ps1", "r_ps1", "i_ps1", "z_ps1", "y_ps1"]
        fluxes = np.array([catalog[col][cc] for col in ("flux_g", "flux_r", "flux_i", "flux_z", "flux_y")])
        errors = np.array([catalog[col][cc] for col in ("e_flux_g", "e_flux_r", "e_flux_i", "e_flux_z", "e_flux_y")])
        for name in ("fiberFlux", "psfFlux", "totalFlux"):
            getattr(design, name)[dd] = fluxes
            getattr(design, name + "Err")[dd] = errors

    select = (design.spectrograph != 1)
    design.targetType[select] = TargetType.SKY
    design.catId[select] = 0
    startObjId = design.objId[(design.spectrograph == 1) & (design.catId == 0)].max()
    design.objId[select] = np.arange(startObjId + 1, startObjId + 1 + select.sum())
    for index in np.argwhere(select)[0]:
        design.filterNames[index] = []
        for name in ("fiberFlux", "psfFlux", "totalFlux"):
            getattr(design, name)[index] = np.array([], dtype=float)
            getattr(design, name + "Err")[index] = np.array([], dtype=float)

-----

Integration test.

In [76]:
design = PfsDesign.read(1, "/home/pfs/pfs/drp_stella_data/raw")
select = (design.spectrograph == 1) & (design.fiberStatus == FiberStatus.GOOD)
updatePfsDesign(design, np.array([103, 170, 182]))
design.write("/home/pfs/pfs/sim2d-151/integrationTest_fixed/")

In [75]:
select = (design.spectrograph == 1) & (design.fiberStatus == FiberStatus.GOOD)
print(design.fiberId[select])
print(design.catId[select])
print(design.objId[select])

[  2  42  84 127 169 212 254 296 357 399 441 484 526 569 611]
[9 1 0 0 9 1 1 1 0 0 9 1 0 1 1]
[103  71   8   6 170  93  55 105   5   7 182  94   4  18  76]


-----

Now for the weekly and science sets!

In [58]:
weekly = PfsDesign.read(1, "/home/pfs/pfs/sim2d-151/weekly")
science1 = PfsDesign.read(9, "/home/pfs/pfs/sim2d-151/science")
science2 = PfsDesign.read(10, "/home/pfs/pfs/sim2d-151/science")

In [59]:
weeklyObjId = np.arange(100, 160, dtype=int)
np.random.shuffle(weeklyObjId)
updatePfsDesign(weekly, weeklyObjId)

scienceObjId = np.arange(141, 200, dtype=int)
np.random.shuffle(scienceObjId)
updatePfsDesign(science1, scienceObjId)
scienceObjId = scienceObjId.copy()
np.random.shuffle(scienceObjId)
updatePfsDesign(science2, scienceObjId)

weekly.write("/home/pfs/pfs/sim2d-151/weekly_fixed/")
science1.write("/home/pfs/pfs/sim2d-151/science_fixed/")
science2.write("/home/pfs/pfs/sim2d-151/science_fixed/")